In [128]:
from bs4 import BeautifulSoup as soup
from requests import get
import pandas as pd
import numpy as np
import requests
import re
from tqdm import tqdm

In [3]:
doctors = []
for i in tqdm(range(1,1307)):
  url = 'https://www.drdata.in/list-doctors.php?state=Madhya%20Pradesh&city=Indore&page='+str(i)
  r = requests.get(url)
  page_html = soup(r.text, 'html.parser') 
  table = page_html.find("table",class_="table-bordered table-striped table-condensed cf").find('tbody')
  for i in table.find_all("tr"):
    #print(i)
    name,spec, degree, state, city, details = i.find_all('td')
    doctors.append([name.text, spec.text, degree.text, state.text, city.text, "https://www.drdata.in/"+details.find('a', href=True)['href']])
doctors

 30%|███████████████████████▉                                                       | 396/1306 [04:51<11:10,  1.36it/s]


KeyboardInterrupt: 

In [ ]:
df = pd.DataFrame(doctors,columns=["Name", 'Speciality', 'Degree', 'City', 'State', 'Details'])
df

In [ ]:
df.to_csv('./Data/doctor_data.csv', index = False)

In [ ]:
df = pd.read_csv('./Data/doctor_data.csv')
df

In [3]:
invalid = []
doctorDetails = []
for i in tqdm(range(len(df))):
  try:
    url = df['Details'][i]
    #print(url)
    r = requests.get(url)
    page_html = soup(r.text, 'html.parser') 
    table = page_html.find("table",class_="table-bordered table-striped table-condensed cf")
    #print(page_html.find(class_ = 'wp-r'))
    vote = page_html.find('div', {"class" : 'wp-r'}).text.replace(' vote', '') if page_html.find('div', class_ = 'wp-r') else 0
    rating = page_html.find('span', class_ = 'wp-rating-score').text if page_html.find('span', class_ = 'wp-rating-score') else 0
    
    detail = [i.text for i in table.find_all('td')] + ['Rating', rating, 'Votes', vote]
    doctorDetails.append(detail)
  except:
    invalid.append(i)
    pass
doctorDetails

100%|██████████| 4273/4273 [1:15:34<00:00,  1.06s/it]


[['Name',
  'Dr. Aanjne Rajendra Kumar',
  'Specialization',
  'Oncologist-Radiation',
  'Degree',
  'MBBS, MD (Radiation-Oncology)',
  'Area of Practice',
  'Radiation Oncology and Chemotherapy',
  'Clinic/ Hospital Name',
  'Choithram Hospital and Research Centre',
  'Date of Birth',
  '0000-04-16',
  'Address',
  'Institute Of Cancer Sciences Choithram Hospital and Research Centre, Manikbag Road, Indore\nTime-9:00am To 5:00pm\nAdd2-Chothram Clinic, Annapurna Road, Indore\nTime-5:00pm To 7:00pm',
  'State',
  'Madhya Pradesh',
  'District',
  ' Indore',
  'Geographical Area',
  'Manik Bagh Road',
  'About Doctor',
  '\xa0',
  'Rating',
  0,
  'Votes',
  0],
 ['Name',
  'Dr. Abbas Shahid',
  'Specialization',
  'Nephrologist',
  'Degree',
  'MBBS, MD DNB (Nephrology)',
  'Area of Practice',
  'Nephrology, Kidney Specialist',
  'Date of Birth',
  '0000-00-00',
  'Address',
  '21, Babji Nagar, Behind Sagar Automobile, Indore',
  'State',
  'Madhya Pradesh',
  'District',
  ' Indore',
  

In [4]:
len(doctorDetails)

4065

In [5]:
refined_details = []
for i in doctorDetails:
  details = {}
  for j in range(0,len(i),2):
    details[i[j]] = i[j+1]
  refined_details.append(details)
refined_details

[{'About Doctor': '\xa0',
  'Address': 'Institute Of Cancer Sciences Choithram Hospital and Research Centre, Manikbag Road, Indore\nTime-9:00am To 5:00pm\nAdd2-Chothram Clinic, Annapurna Road, Indore\nTime-5:00pm To 7:00pm',
  'Area of Practice': 'Radiation Oncology and Chemotherapy',
  'Clinic/ Hospital Name': 'Choithram Hospital and Research Centre',
  'Date of Birth': '0000-04-16',
  'Degree': 'MBBS, MD (Radiation-Oncology)',
  'District': ' Indore',
  'Geographical Area': 'Manik Bagh Road',
  'Name': 'Dr. Aanjne Rajendra Kumar',
  'Rating': 0,
  'Specialization': 'Oncologist-Radiation',
  'State': 'Madhya Pradesh',
  'Votes': 0},
 {' Member of': '',
  'About Doctor': '\xa0',
  'Address': '21, Babji Nagar, Behind Sagar Automobile, Indore',
  'Area of Practice': 'Nephrology, Kidney Specialist',
  'Date of Birth': '0000-00-00',
  'Degree': 'MBBS, MD DNB (Nephrology)',
  'District': ' Indore',
  'Geographical Area': 'AB Road',
  'Name': 'Dr. Abbas Shahid',
  'Rating': 0,
  'Specializat

In [6]:
df = pd.DataFrame(refined_details)
df

Name  ...  Practicing Since
0     Dr. Aanjne Rajendra Kumar  ...               NaN
1              Dr. Abbas Shahid  ...               NaN
2               Dr. Abdul Malik  ...               NaN
3        Dr. Acharya Charulata   ...               NaN
4              Dr. Acharya D.C.  ...               NaN
...                         ...  ...               ...
4060        Mrs. Tripathi Priti  ...               NaN
4061         Mrs. Tripathi Usha  ...               NaN
4062    Mrs. Vijaywargiya Vidhi  ...               NaN
4063        Mrs. Vinita Jaiswal  ...               NaN
4064          Ms. Nadeem Zainab  ...               NaN

[4065 rows x 28 columns]

In [7]:
df.isnull().sum()

Name                          0
Specialization                0
Degree                       10
Area of Practice             93
Clinic/ Hospital Name      2173
Date of Birth                 0
Address                       9
State                         0
District                      0
Geographical Area           371
About Doctor                823
Rating                        0
Votes                         0
 Member of                 2443
Phone Number               2341
Mobile Number and Email    2341
Address2                   1473
Management                 3520
Practice as                3633
Website                    3937
Graduation Course          4026
Post Graduation Course     4036
Name of Medical Council    4000
Registration Number        4000
Pin Code                   3242
Fax Number                 4043
After PG Course            4051
 Practicing Since          4062
dtype: int64

In [9]:
df.to_csv('./Data/doctor_details.csv', index=False)

In [9]:
df.shape

(4065, 28)

In [140]:
df = pd.read_csv('./Data/doctor_details.csv')
df.head()

Name               Specialization  \
0  Dr. Aanjne Rajendra Kumar         Oncologist-Radiation   
1           Dr. Abbas Shahid                 Nephrologist   
2            Dr. Abdul Malik  Allopathic Family Physician   
3     Dr. Acharya Charulata                 Gynaecologist   
4           Dr. Acharya D.C.                 AYUSH Doctor   

                          Degree                     Area of Practice  \
0  MBBS, MD (Radiation-Oncology)  Radiation Oncology and Chemotherapy   
1      MBBS, MD DNB (Nephrology)        Nephrology, Kidney Specialist   
2                           MBBS           Allopathic Family Medicine   
3                      MBBS, DGO                          Gynaecology   
4                           BAMS                   Ayurved Specialist   

                    Clinic/ Hospital Name Date of Birth  \
0  Choithram Hospital and Research Centre    0000-04-16   
1                                     NaN    0000-00-00   
2                  Dr. Abdul Malik Clinic    0000-00-00   
3                Chaitanya Clinic, Indore    0000-00-00   
4                                     NaN    1945-05-21   

                                             Address           State District  \
0  Institute Of Cancer Sciences Choithram Hospita...  Madhya Pradesh   Indore   
1   21, Babji Nagar, Behind Sagar Automobile, Indore  Madhya Pradesh   Indore   
2  Dr. Abdul Malik Clinic, Patti Bazar, Mhow, Dis...  Madhya Pradesh   Indore   
3   Chaitanya Clinic, 42, G/G, Scheme No. 54, Indore  Madhya Pradesh   Indore   
4                       39, Sirpur Dhar Road, Indore  Madhya Pradesh   Indore   

  Geographical Area  ... Practice as  Website  Graduation Course  \
0   Manik Bagh Road  ...         NaN      NaN                NaN   
1           AB Road  ...         NaN      NaN                NaN   
2             Mhow   ...         NaN      NaN                NaN   
3      Vijay Nagar   ...         NaN      NaN                NaN   
4         Dhar Road  ...         NaN      NaN                NaN   

  Post Graduation Course Name of Medical Council Registration Number Pin Code  \
0                    NaN                     NaN                 NaN      NaN   
1                    NaN                     NaN                 NaN      NaN   
2                    NaN                     NaN                 NaN      NaN   
3                    NaN                     NaN                 NaN      NaN   
4                    NaN                     NaN                 NaN      NaN   

  Fax Number After PG Course  Practicing Since  
0        NaN             NaN               NaN  
1        NaN             NaN               NaN  
2        NaN             NaN               NaN  
3        NaN             NaN               NaN  
4        NaN             NaN               NaN  

[5 rows x 28 columns]

In [99]:
del df['Geographical Area']

In [103]:
df.isnull().sum()

Name                        0
Specialization              0
Degree                      0
Area of Practice           93
Clinic/ Hospital Name       0
Date of Birth               0
Address                     0
State                       0
District                    0
Rating                      0
Votes                       0
Phone Number                0
Name of Medical Council     0
Registration Number         0
Pin Code                    0
 Practicing Since           0
latitude                    0
longitude                   0
dtype: int64

In [102]:
df['Degree'] = df['Degree'].fillna('MBBS')
df['Clinic/ Hospital Name'] = df['Clinic/ Hospital Name'].fillna('Not Given')
df['Name of Medical Council'] = df['Name of Medical Council'].fillna('Not Given')
df['Address'] = df['Address'].fillna('Madhya Pradesh Medical Council')
df[' Practicing Since'] = df[' Practicing Since'].fillna('2008')
df['Registration Number'] = df['Registration Number'].fillna('Not Given')
df['Phone Number'] = df['Phone Number'].fillna('Not Given')


In [45]:

from urllib.parse import urlencode

In [89]:
latitudes = []
longitudes = []
pincodes = []
for i in tqdm(df.index):
    address = str(df['Address'][i]).split('\n')[0]
    address = address.split()
    n = len(address)
    address = ' '.join(address[n//2-2:n//2])
    payload = {'address':address}
    result = urlencode(payload)
    new_address = result[result.index('=')+1:]
    new_address = new_address.replace('+', '%20')
    new_address += '%20'
    
    #print(new_address)
    response = requests.get("https://api.tomtom.com/search/2/geocode/"+new_address+".json?typeahead=true&countrySet=IN&lat=22.71574&lon=75.85571&radius=500000&key=D9T3HvijBqZXoLVYE3ClkLlWw7WGuF1k")
    data = response.json()
    bias = data["summary"]['geoBias']
    latitude,longitude = float(bias['lat']),float(bias['lon'])
    pincode = 452001
    if len(data['results']) > 0:
        points = data['results'][0]
        latitude,longitude = float(points['position']['lat']),float(points['position']['lon'])
        if 'postalCode' in points['address']: 
            pincode = int(points['address']['postalCode'].split(',')[0])
    
    latitudes.append(latitude)
    longitudes.append(longitude)
    pincodes.append(pincode)

latitudes

 60%|██████████████████████████████████████████████▉                               | 2445/4065 [27:32<18:14,  1.48it/s]


JSONDecodeError: Expecting value: line 1 column 1 (char 0)

In [95]:
latitudes += [22.71574] * (4065 - len(latitudes))
longitudes += [75.85571] * (4065 - len(longitudes))
pincodes += [452001] * (4065 - len(pincodes))


In [100]:
df['latitude'] = latitudes
df['longitude'] = longitudes
df['Pin Code'] = pincodes

df.head()

Name               Specialization  \
0  Dr. Aanjne Rajendra Kumar         Oncologist-Radiation   
1           Dr. Abbas Shahid                 Nephrologist   
2            Dr. Abdul Malik  Allopathic Family Physician   
3     Dr. Acharya Charulata                 Gynaecologist   
4           Dr. Acharya D.C.                 AYUSH Doctor   

                          Degree                     Area of Practice  \
0  MBBS, MD (Radiation-Oncology)  Radiation Oncology and Chemotherapy   
1      MBBS, MD DNB (Nephrology)        Nephrology, Kidney Specialist   
2                           MBBS           Allopathic Family Medicine   
3                      MBBS, DGO                          Gynaecology   
4                           BAMS                   Ayurved Specialist   

                    Clinic/ Hospital Name Date of Birth  \
0  Choithram Hospital and Research Centre    0000-04-16   
1                               Not Given    0000-00-00   
2                  Dr. Abdul Malik Clinic    0000-00-00   
3                Chaitanya Clinic, Indore    0000-00-00   
4                               Not Given    1945-05-21   

                                             Address           State District  \
0  Institute Of Cancer Sciences Choithram Hospita...  Madhya Pradesh   Indore   
1   21, Babji Nagar, Behind Sagar Automobile, Indore  Madhya Pradesh   Indore   
2  Dr. Abdul Malik Clinic, Patti Bazar, Mhow, Dis...  Madhya Pradesh   Indore   
3   Chaitanya Clinic, 42, G/G, Scheme No. 54, Indore  Madhya Pradesh   Indore   
4                       39, Sirpur Dhar Road, Indore  Madhya Pradesh   Indore   

   Rating  Votes  Phone Number Name of Medical Council Registration Number  \
0       0      0           NaN               Not Given           Not Given   
1       0      0           NaN               Not Given           Not Given   
2       0      0           NaN               Not Given           Not Given   
3       0      0  0731-2553745               Not Given           Not Given   
4       0      0  0731-2382317               Not Given           Not Given   

   Pin Code  Practicing Since  latitude  longitude  
0    452001              2008  22.71638   75.87482  
1    422011              2008  19.98225   73.80490  
2    311404              2008  25.61871   74.91918  
3    452002              2008  22.71436   75.84702  
4    452001              2008  19.33749   78.97032

In [119]:
genders

['MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'FEMALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'FEMALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE

In [121]:
gender = 'MALE'

for i in tqdm(df.index[972:]):
    if 'Miss' in df["Name"][i] or 'Mrs.' in df["Name"][i] or 'Ms.' in df["Name"][i] :
        gender = 'Female'
    elif 'Mr.' in df["Name"][i] or 'Master' in df["Name"][i]:
        gender = 'Male'
    else:
        name = df["Name"][i].split(" ")
        firstName = name[1]
        url = "https://api.genderize.io/?name="+firstName
        response = requests.get(url)
        if 'gender' in response.json():
            gender = response.json()['gender'] if response.json()['gender'] else 'male'
        else:
            gender = 'Male'
        #print(response.json())

    gender = gender.upper()
    genders.append(gender)

genders

100%|██████████████████████████████████████████████████████████████████████████████| 3093/3093 [55:45<00:00,  1.08s/it]


['MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'FEMALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'FEMALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE',
 'MALE

In [123]:
df['gender'] =genders
df.head()

Name               Specialization  \
0  Dr. Aanjne Rajendra Kumar         Oncologist-Radiation   
1           Dr. Abbas Shahid                 Nephrologist   
2            Dr. Abdul Malik  Allopathic Family Physician   
3     Dr. Acharya Charulata                 Gynaecologist   
4           Dr. Acharya D.C.                 AYUSH Doctor   

                          Degree                     Area of Practice  \
0  MBBS, MD (Radiation-Oncology)  Radiation Oncology and Chemotherapy   
1      MBBS, MD DNB (Nephrology)        Nephrology, Kidney Specialist   
2                           MBBS           Allopathic Family Medicine   
3                      MBBS, DGO                          Gynaecology   
4                           BAMS                   Ayurved Specialist   

                    Clinic/ Hospital Name Date of Birth  \
0  Choithram Hospital and Research Centre    0000-04-16   
1                               Not Given    0000-00-00   
2                  Dr. Abdul Malik Clinic    0000-00-00   
3                Chaitanya Clinic, Indore    0000-00-00   
4                               Not Given    1945-05-21   

                                             Address           State District  \
0  Institute Of Cancer Sciences Choithram Hospita...  Madhya Pradesh   Indore   
1   21, Babji Nagar, Behind Sagar Automobile, Indore  Madhya Pradesh   Indore   
2  Dr. Abdul Malik Clinic, Patti Bazar, Mhow, Dis...  Madhya Pradesh   Indore   
3   Chaitanya Clinic, 42, G/G, Scheme No. 54, Indore  Madhya Pradesh   Indore   
4                       39, Sirpur Dhar Road, Indore  Madhya Pradesh   Indore   

   Rating  Votes  Phone Number Name of Medical Council Registration Number  \
0       0      0     Not Given               Not Given           Not Given   
1       0      0     Not Given               Not Given           Not Given   
2       0      0     Not Given               Not Given           Not Given   
3       0      0  0731-2553745               Not Given           Not Given   
4       0      0  0731-2382317               Not Given           Not Given   

   Pin Code  Practicing Since  latitude  longitude gender  
0    452001              2008  22.71638   75.87482   MALE  
1    422011              2008  19.98225   73.80490   MALE  
2    311404              2008  25.61871   74.91918   MALE  
3    452002              2008  22.71436   75.84702   MALE  
4    452001              2008  19.33749   78.97032   MALE

In [125]:
df['Date of Birth'] = df['Date of Birth'].str.replace("0000", '1978')
df['Date of Birth'] = df['Date of Birth'].str.replace("00", '12')
df.head()

Name               Specialization  \
0  Dr. Aanjne Rajendra Kumar         Oncologist-Radiation   
1           Dr. Abbas Shahid                 Nephrologist   
2            Dr. Abdul Malik  Allopathic Family Physician   
3     Dr. Acharya Charulata                 Gynaecologist   
4           Dr. Acharya D.C.                 AYUSH Doctor   

                          Degree                     Area of Practice  \
0  MBBS, MD (Radiation-Oncology)  Radiation Oncology and Chemotherapy   
1      MBBS, MD DNB (Nephrology)        Nephrology, Kidney Specialist   
2                           MBBS           Allopathic Family Medicine   
3                      MBBS, DGO                          Gynaecology   
4                           BAMS                   Ayurved Specialist   

                    Clinic/ Hospital Name Date of Birth  \
0  Choithram Hospital and Research Centre    1978-04-16   
1                               Not Given    1978-12-12   
2                  Dr. Abdul Malik Clinic    1978-12-12   
3                Chaitanya Clinic, Indore    1978-12-12   
4                               Not Given    1945-05-21   

                                             Address           State District  \
0  Institute Of Cancer Sciences Choithram Hospita...  Madhya Pradesh   Indore   
1   21, Babji Nagar, Behind Sagar Automobile, Indore  Madhya Pradesh   Indore   
2  Dr. Abdul Malik Clinic, Patti Bazar, Mhow, Dis...  Madhya Pradesh   Indore   
3   Chaitanya Clinic, 42, G/G, Scheme No. 54, Indore  Madhya Pradesh   Indore   
4                       39, Sirpur Dhar Road, Indore  Madhya Pradesh   Indore   

   Rating  Votes  Phone Number Name of Medical Council Registration Number  \
0       0      0     Not Given               Not Given           Not Given   
1       0      0     Not Given               Not Given           Not Given   
2       0      0     Not Given               Not Given           Not Given   
3       0      0  0731-2553745               Not Given           Not Given   
4       0      0  0731-2382317               Not Given           Not Given   

   Pin Code  Practicing Since  latitude  longitude gender  
0    452001              2008  22.71638   75.87482   MALE  
1    422011              2008  19.98225   73.80490   MALE  
2    311404              2008  25.61871   74.91918   MALE  
3    452002              2008  22.71436   75.84702   MALE  
4    452001              2008  19.33749   78.97032   MALE

In [129]:
df['Rating'] = np.random.randint(1, 6, df.shape[0])
df['Votes'] = np.random.randint(100, 6000, df.shape[0])
df.head()

Name               Specialization  \
0  Dr. Aanjne Rajendra Kumar         Oncologist-Radiation   
1           Dr. Abbas Shahid                 Nephrologist   
2            Dr. Abdul Malik  Allopathic Family Physician   
3     Dr. Acharya Charulata                 Gynaecologist   
4           Dr. Acharya D.C.                 AYUSH Doctor   

                          Degree                     Area of Practice  \
0  MBBS, MD (Radiation-Oncology)  Radiation Oncology and Chemotherapy   
1      MBBS, MD DNB (Nephrology)        Nephrology, Kidney Specialist   
2                           MBBS           Allopathic Family Medicine   
3                      MBBS, DGO                          Gynaecology   
4                           BAMS                   Ayurved Specialist   

                    Clinic/ Hospital Name Date of Birth  \
0  Choithram Hospital and Research Centre    1978-04-16   
1                               Not Given    1978-12-12   
2                  Dr. Abdul Malik Clinic    1978-12-12   
3                Chaitanya Clinic, Indore    1978-12-12   
4                               Not Given    1945-05-21   

                                             Address           State District  \
0  Institute Of Cancer Sciences Choithram Hospita...  Madhya Pradesh   Indore   
1   21, Babji Nagar, Behind Sagar Automobile, Indore  Madhya Pradesh   Indore   
2  Dr. Abdul Malik Clinic, Patti Bazar, Mhow, Dis...  Madhya Pradesh   Indore   
3   Chaitanya Clinic, 42, G/G, Scheme No. 54, Indore  Madhya Pradesh   Indore   
4                       39, Sirpur Dhar Road, Indore  Madhya Pradesh   Indore   

   Rating  Votes  Phone Number Name of Medical Council Registration Number  \
0       4   3142     Not Given               Not Given           Not Given   
1       5    103     Not Given               Not Given           Not Given   
2       1   5014     Not Given               Not Given           Not Given   
3       2   2739  0731-2553745               Not Given           Not Given   
4       5   2457  0731-2382317               Not Given           Not Given   

   Pin Code  Practicing Since  latitude  longitude gender  
0    452001              2008  22.71638   75.87482   MALE  
1    422011              2008  19.98225   73.80490   MALE  
2    311404              2008  25.61871   74.91918   MALE  
3    452002              2008  22.71436   75.84702   MALE  
4    452001              2008  19.33749   78.97032   MALE

In [134]:
df['Country'] = "India"
df.head()

Name               Specialization  \
0  Dr. Aanjne Rajendra Kumar         Oncologist-Radiation   
1           Dr. Abbas Shahid                 Nephrologist   
2            Dr. Abdul Malik  Allopathic Family Physician   
3     Dr. Acharya Charulata                 Gynaecologist   
4           Dr. Acharya D.C.                 AYUSH Doctor   

                          Degree                     Area of Practice  \
0  MBBS, MD (Radiation-Oncology)  Radiation Oncology and Chemotherapy   
1      MBBS, MD DNB (Nephrology)        Nephrology, Kidney Specialist   
2                           MBBS           Allopathic Family Medicine   
3                      MBBS, DGO                          Gynaecology   
4                           BAMS                   Ayurved Specialist   

                    Clinic/ Hospital Name Date of Birth  \
0  Choithram Hospital and Research Centre    1978-04-16   
1                               Not Given    1978-12-12   
2                  Dr. Abdul Malik Clinic    1978-12-12   
3                Chaitanya Clinic, Indore    1978-12-12   
4                               Not Given    1945-05-21   

                                             Address           State District  \
0  Institute Of Cancer Sciences Choithram Hospita...  Madhya Pradesh   Indore   
1   21, Babji Nagar, Behind Sagar Automobile, Indore  Madhya Pradesh   Indore   
2  Dr. Abdul Malik Clinic, Patti Bazar, Mhow, Dis...  Madhya Pradesh   Indore   
3   Chaitanya Clinic, 42, G/G, Scheme No. 54, Indore  Madhya Pradesh   Indore   
4                       39, Sirpur Dhar Road, Indore  Madhya Pradesh   Indore   

   Rating  Votes  Phone Number Name of Medical Council Registration Number  \
0       4   3142     Not Given               Not Given           Not Given   
1       5    103     Not Given               Not Given           Not Given   
2       1   5014     Not Given               Not Given           Not Given   
3       2   2739  0731-2553745               Not Given           Not Given   
4       5   2457  0731-2382317               Not Given           Not Given   

   Pin Code  Practicing Since  latitude  longitude gender Country  
0    452001              2008  22.71638   75.87482   MALE   India  
1    422011              2008  19.98225   73.80490   MALE   India  
2    311404              2008  25.61871   74.91918   MALE   India  
3    452002              2008  22.71436   75.84702   MALE   India  
4    452001              2008  19.33749   78.97032   MALE   India

In [145]:
columns = []
for col in df.columns:
    name = ''.join(word.title() for word in col.split())
    columns.append(name[0].lower() + name[1:])
df.columns = columns

df.head()

name               specialization  \
0  Dr. Aanjne Rajendra Kumar         Oncologist-Radiation   
1           Dr. Abbas Shahid                 Nephrologist   
2            Dr. Abdul Malik  Allopathic Family Physician   
3     Dr. Acharya Charulata                 Gynaecologist   
4           Dr. Acharya D.C.                 AYUSH Doctor   

                          degree                       areaOfPractice  \
0  MBBS, MD (Radiation-Oncology)  Radiation Oncology and Chemotherapy   
1      MBBS, MD DNB (Nephrology)        Nephrology, Kidney Specialist   
2                           MBBS           Allopathic Family Medicine   
3                      MBBS, DGO                          Gynaecology   
4                           BAMS                   Ayurved Specialist   

                      clinic/HospitalName dateOfBirth  \
0  Choithram Hospital and Research Centre  1978-04-16   
1                               Not Given  1978-12-12   
2                  Dr. Abdul Malik Clinic  1978-12-12   
3                Chaitanya Clinic, Indore  1978-12-12   
4                               Not Given  1945-05-21   

                                             address           state district  \
0  Institute Of Cancer Sciences Choithram Hospita...  Madhya Pradesh   Indore   
1   21, Babji Nagar, Behind Sagar Automobile, Indore  Madhya Pradesh   Indore   
2  Dr. Abdul Malik Clinic, Patti Bazar, Mhow, Dis...  Madhya Pradesh   Indore   
3   Chaitanya Clinic, 42, G/G, Scheme No. 54, Indore  Madhya Pradesh   Indore   
4                       39, Sirpur Dhar Road, Indore  Madhya Pradesh   Indore   

   rating  votes   phoneNumber nameOfMedicalCouncil registrationNumber  \
0       4   3142     Not Given            Not Given          Not Given   
1       5    103     Not Given            Not Given          Not Given   
2       1   5014     Not Given            Not Given          Not Given   
3       2   2739  0731-2553745            Not Given          Not Given   
4       5   2457  0731-2382317            Not Given          Not Given   

   pinCode  practicingSince  latitude  longitude gender  
0   452001           2008.0  22.71638   75.87482   MALE  
1   422011           2008.0  19.98225   73.80490   MALE  
2   311404           2008.0  25.61871   74.91918   MALE  
3   452002           2008.0  22.71436   75.84702   MALE  
4   452001           2008.0  19.33749   78.97032   MALE

In [146]:
df.to_csv('./Data/refined_doctor_details.csv', index=False)

In [144]:
df = pd.read_csv('./Data/refined_doctor_details.csv')

In [167]:
dtos = []
for i in tqdm(df.index):
    data = {
      "address": {
        "city": df['district'][i],
        "country": "India",
        "latitude": round(df['latitude'][i],3),
        "longitude": round(df['longitude'][i],3),
        "pinCode": int(df['pinCode'][i]),
        "state": df['state'][i],
        "street": df['address'][i]
      },
      "age": int(2021 - int(df['dateOfBirth'][i].split('-')[0])),
      "clinicName": [
        df['clinic/HospitalName'][i]
      ],
      "dateOfBirth": df['dateOfBirth'][i],
      "degree": df['degree'][i].split(','),
      "gender": df['gender'][i],
      "medicalCouncilAffiliation": [
        df['nameOfMedicalCouncil'][i]
      ],
      "emailId" : ''.join(df['name'][i].split()).lower() + '@gmail.com',
      "name": df['name'][i],
      "phoneNumber": df['phoneNumber'][i],
      "rating": int(df['rating'][i]),
      "registrationNumber": df['registrationNumber'][i],
      "specialization": [
        df['specialization'][i]
      ],
      "yearOfExperience": int(2021 - int(df['practicingSince'][i]))
    }
    dtos.append(data)
dtos[:10]


100%|████████████████████████████████████████████████████████████████████████████| 4065/4065 [00:00<00:00, 5508.14it/s]


[{'address': {'city': ' Indore',
   'country': 'India',
   'latitude': 22.716,
   'longitude': 75.875,
   'pinCode': 452001,
   'state': 'Madhya Pradesh',
   'street': 'Institute Of Cancer Sciences Choithram Hospital and Research Centre, Manikbag Road, Indore\nTime-9:00am To 5:00pm\nAdd2-Chothram Clinic, Annapurna Road, Indore\nTime-5:00pm To 7:00pm'},
  'age': 43,
  'clinicName': ['Choithram Hospital and Research Centre'],
  'dateOfBirth': '1978-04-16',
  'degree': ['MBBS', ' MD (Radiation-Oncology)'],
  'gender': 'MALE',
  'medicalCouncilAffiliation': ['Not Given'],
  'emailId': 'dr.aanjnerajendrakumar@gmail.com',
  'name': 'Dr. Aanjne Rajendra Kumar',
  'phoneNumber': 'Not Given',
  'rating': 4,
  'registrationNumber': 'Not Given',
  'specialization': ['Oncologist-Radiation'],
  'yearOfExperience': 13},
 {'address': {'city': ' Indore',
   'country': 'India',
   'latitude': 19.982,
   'longitude': 73.805,
   'pinCode': 422011,
   'state': 'Madhya Pradesh',
   'street': '21, Babji Nag

In [152]:
import json

In [168]:
for body in tqdm(dtos):
    body = json.dumps(body)
    headers = {
        'Content-Type': 'application/json'
    }
    url = 'http://20.198.81.29:8080/doctor'
    x = requests.post(url, data=body, headers=headers)
    print(x.status_code, x.json())

  0%|                                                                                 | 1/4065 [00:00<12:35,  5.38it/s]

200 {'id': 7201, 'name': 'Dr. Aanjne Rajendra Kumar', 'emailId': 'dr.aanjnerajendrakumar@gmail.com', 'phoneNumber': 'Not Given', 'gender': 'MALE', 'dateOfBirth': '1978-04-16', 'age': 43, 'address': {'street': 'Institute Of Cancer Sciences Choithram Hospital and Research Centre, Manikbag Road, Indore\nTime-9:00am To 5:00pm\nAdd2-Chothram Clinic, Annapurna Road, Indore\nTime-5:00pm To 7:00pm', 'city': ' Indore', 'state': 'Madhya Pradesh', 'country': 'India', 'pinCode': 452001, 'latitude': 22.716, 'longitude': 75.875}, 'specialization': ['Oncologist-Radiation'], 'degree': ['MBBS', ' MD (Radiation-Oncology)'], 'medicalCouncilAffiliation': ['Not Given'], 'clinicName': ['Choithram Hospital and Research Centre'], 'registrationNumber': 'Not Given', 'rating': 4, 'yearOfExperience': 13, 'links': [{'rel': 'self', 'href': 'http://20.198.81.29:8080/doctor/7201'}]}
200

  0%|                                                                                 | 3/4065 [00:00<11:23,  5.94it/s]

 {'id': 7202, 'name': 'Dr. Abbas Shahid', 'emailId': 'dr.abbasshahid@gmail.com', 'phoneNumber': 'Not Given', 'gender': 'MALE', 'dateOfBirth': '1978-12-12', 'age': 43, 'address': {'street': '21, Babji Nagar, Behind Sagar Automobile, Indore', 'city': ' Indore', 'state': 'Madhya Pradesh', 'country': 'India', 'pinCode': 422011, 'latitude': 19.982, 'longitude': 73.805}, 'specialization': ['Nephrologist'], 'degree': ['MBBS', ' MD DNB (Nephrology)'], 'medicalCouncilAffiliation': ['Not Given'], 'clinicName': ['Not Given'], 'registrationNumber': 'Not Given', 'rating': 5, 'yearOfExperience': 13, 'links': [{'rel': 'self', 'href': 'http://20.198.81.29:8080/doctor/7202'}]}
200 {'id': 7203, 'name': 'Dr. Abdul Malik', 'emailId': 'dr.abdulmalik@gmail.com', 'phoneNumber': 'Not Given', 'gender': 'MALE', 'dateOfBirth': '1978-12-12', 'age': 43, 'address': {'street': 'Dr. Abdul Malik Clinic, Patti Bazar, Mhow, Dist. Indore', 'city': ' Indore', 'state': 'Madhya Pradesh', 'country': 'India', 'pinCode': 31140

  0%|                                                                                 | 5/4065 [00:00<09:42,  6.97it/s]

...

200 {'id': 11175, 'name': 'Mrs. Shukla Priti', 'emailId': 'mrs.shuklapriti@gmail.com', 'phoneNumber': '0731-2590444', 'gender': 'FEMALE', 'dateOfBirth': '1978-12-12', 'age': 43, 'address': {'street': 'Mohak Super Speciality, Ujjain Sanwer Road, Indore', 'city': ' Indore', 'state': 'Madhya Pradesh', 'country': 'India', 'pinCode': 452001, 'latitude': 22.716, 'longitude': 75.856}, 'specialization': ['Dietician'], 'degree': ['MSc (Food & Nutrition)'], 'medicalCouncilAffiliation': ['Not Given'], 'clinicName': ['Not Given'], 'registrationNumber': 'Not Given', 'rating': 3, 'yearOfExperience': 13, 'links': [{'rel': 'self', 'href': 'http://20.198.81.29:8080/doctor/11175'}]}
200 {'id': 11176, 'name': 'Mrs. Tripathi Priti', 'emailId': 'mrs.tripathipriti@gmail.com', 'phoneNumber': 'Not Given', 'gender': 'FEMALE', 'dateOfBirth': '1978-12-12', 'age': 43, 'address': {'street': 'LCH Hospital, Scheme No.78, Indore', 'city': ' Indore', 'state': 'Madhya Pradesh', 'country': 'India', 'pinCode': 452001, 'l

100%|█████████████████████████████████████████████████████████████████████████████▉| 4063/4065 [08:09<00:00,  9.06it/s]

200 {'id': 11177, 'name': 'Mrs. Tripathi Usha', 'emailId': 'mrs.tripathiusha@gmail.com', 'phoneNumber': 'Not Given', 'gender': 'FEMALE', 'dateOfBirth': '1978-12-12', 'age': 43, 'address': {'street': 'Totall Diabetes Hormone Institute, BCM, Health Island, PU-4, Scheme No.54, Indore', 'city': ' Indore', 'state': 'Madhya Pradesh', 'country': 'India', 'pinCode': 452001, 'latitude': 22.716, 'longitude': 75.856}, 'specialization': ['Dietician'], 'degree': ['MSc (Food & Nutrition)'], 'medicalCouncilAffiliation': ['Not Given'], 'clinicName': ['Totall Diabetes Hormone Institute, Indore'], 'registrationNumber': 'Not Given', 'rating': 4, 'yearOfExperience': 13, 'links': [{'rel': 'self', 'href': 'http://20.198.81.29:8080/doctor/11177'}]}
200 {'id': 11178, 'name': 'Mrs. Vijaywargiya Vidhi', 'emailId': 'mrs.vijaywargiyavidhi@gmail.com', 'phoneNumber': 'Not Given', 'gender': 'FEMALE', 'dateOfBirth': '1978-12-12', 'age': 43, 'address': {'street': 'Vidyapati, Race Course Road, Indore', 'city': ' Indore

100%|██████████████████████████████████████████████████████████████████████████████| 4065/4065 [08:09<00:00,  8.30it/s]

200 {'id': 11179, 'name': 'Mrs. Vinita Jaiswal', 'emailId': 'mrs.vinitajaiswal@gmail.com', 'phoneNumber': 'Not Given', 'gender': 'FEMALE', 'dateOfBirth': '1978-04-12', 'age': 43, 'address': {'street': '24, Joy Builders Colony, Inside Rani Sati Gate, YN Road, Indore', 'city': ' Indore', 'state': 'Madhya Pradesh', 'country': 'India', 'pinCode': 452001, 'latitude': 22.716, 'longitude': 75.856}, 'specialization': ['Dietician'], 'degree': ['MSc (Foods & Nutrition)'], 'medicalCouncilAffiliation': ['Not Given'], 'clinicName': ['G.K. Hospital, Indore'], 'registrationNumber': 'Not Given', 'rating': 1, 'yearOfExperience': 13, 'links': [{'rel': 'self', 'href': 'http://20.198.81.29:8080/doctor/11179'}]}
200 {'id': 11180, 'name': 'Ms. Nadeem Zainab', 'emailId': 'ms.nadeemzainab@gmail.com', 'phoneNumber': '0731-4095024', 'gender': 'FEMALE', 'dateOfBirth': '1978-12-12', 'age': 43, 'address': {'street': '34, Saify Nagar, Indore', 'city': ' Indore', 'state': 'Madhya Pradesh', 'country': 'India', 'pinCo